In [1]:
from matdeeplearn.common import data
import os
import torch
import matplotlib.pyplot as plt
from pprint import pprint

from matdeeplearn.preprocessor.helpers import *
from matdeeplearn.preprocessor.transforms import *
from matdeeplearn.common.graph_data import CustomData

from torch_geometric.loader import DataLoader


from ase import neighborlist

%pprint
%load_ext autoreload
%autoreload 2

torch.set_printoptions(profile="full")

/nethome/sbaskaran31/miniconda3/envs/matdeeplearn/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Pretty printing has been turned OFF


In [2]:
dataset = data.get_dataset("/nethome/sbaskaran31/projects/Sidharth/hMOF/raw_5k/")


In [3]:
sample = dataset[0]
sample.n_atoms = torch.tensor([len(sample.x)])


In [63]:
# all neighbors
cells, cell_coors = get_pbc_cells(sample.cell, 1, device="cpu")
distance_matrix, offsets, atom_rij = get_distances(sample.pos, cells, all_neighbors=True)

In [64]:
offsets.shape

torch.Size([257, 257, 27])

In [65]:
distance_matrix.shape

torch.Size([257, 257, 27])

In [66]:
_, indices = torch.topk(distance_matrix, k=1, dim=1, largest=False)

In [67]:
indices.shape

torch.Size([257, 1, 27])

In [68]:
indices[0]

tensor([[256, 254, 251, 238,  11, 233, 226, 224, 221, 112,  32, 107,  38,   0,
          89,  82,  80,  77,  76,  74,  71,  58,  56,  53,  46,  44,  41]])

In [69]:
elems, idx = torch.topk(torch.tensor([[0, 1, 2], [3, 4, 5]]), k=2, dim=1, largest=False)

In [70]:
elems

tensor([[0, 1],
        [3, 4]])

In [71]:
idx

tensor([[0, 1],
        [0, 1]])

In [72]:
indices.shape

torch.Size([257, 1, 27])

In [73]:
indices[0]

tensor([[256, 254, 251, 238,  11, 233, 226, 224, 221, 112,  32, 107,  38,   0,
          89,  82,  80,  77,  76,  74,  71,  58,  56,  53,  46,  44,  41]])

In [74]:
atom_rij.shape

torch.Size([257, 257, 27, 3])

In [75]:
# without all neighbors
cells, cell_coors = get_pbc_cells(sample.cell, 1, device="cpu")
min_atomic_distances, min_indices, rij = get_distances(sample.pos, cells, all_neighbors=False, device="cpu")

In [76]:
min_indices.shape

torch.Size([257, 257, 1])

In [77]:
min_atomic_distances.shape

torch.Size([257, 257, 1])

In [78]:
rij.shape

torch.Size([257, 257, 1, 3])

In [81]:
cd_matrix, offsets = get_cutoff_distance_matrix(sample.pos, sample.cell, 5.0, 50, "cpu", all_neighbors=True)

torch.Size([257, 206, 27])
Unexpected exception formatting exception. Falling back to standard exception


Traceback (most recent call last):
  File "/nethome/sbaskaran31/miniconda3/envs/matdeeplearn/lib/python3.9/site-packages/IPython/core/interactiveshell.py", line 3433, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_223047/1048751462.py", line 1, in <module>
    cd_matrix, offsets = get_cutoff_distance_matrix(sample.pos, sample.cell, 5.0, 50, "cpu", all_neighbors=True)
  File "/net/csefiles/coc-fung-cluster/Sidharth/MatDeepLearn_dev/matdeeplearn/preprocessor/helpers.py", line 295, in get_cutoff_distance_matrix
    cutoff_distance_matrix = threshold_sort(distance_matrix, r, n_neighbors)
  File "/net/csefiles/coc-fung-cluster/Sidharth/MatDeepLearn_dev/matdeeplearn/preprocessor/helpers.py", line 60, in threshold_sort
    A = torch.scatter(
RuntimeError: index 32 is out of bounds for dimension 2 with size 27

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/nethome/sbaskaran31/miniconda3

In [21]:
min_indices.shape

torch.Size([257, 257])

In [5]:
min_atomic_distances1, min_indices1, rij1 = get_distances(sample.pos, cells, all_neighbors=True, device="cpu")

min_atomic_distances torch.Size([257, 257, 27]) min_indices torch.Size([257, 27, 3]) atom_rij torch.Size([257, 257, 27, 3])


In [8]:
min_atomic_distances1[0, 1, :]

tensor([28.9756, 22.1039, 26.2754, 25.2421, 16.9248, 22.1033, 31.4254, 25.2416,
        28.9747, 23.7309, 14.5585, 20.3363, 18.9988,  3.1695, 14.5586, 26.6754,
        18.9989, 23.7310, 28.9748, 22.0938, 26.2593, 25.2501, 16.9251, 22.0945,
        31.4391, 25.2507, 28.9759])

In [ ]:
min_atomic_distances.shape

torch.Size([257, 257])

In [ ]:
cells.shape

torch.Size([27, 3])

In [ ]:
sample.cell_offsets.shape

torch.Size([637, 3])

In [ ]:
rij.shape

torch.Size([257, 257, 3])

In [ ]:
min_indices.shape

torch.Size([257, 257])

In [ ]:
dict(sample.__dict__["_store"]).keys()


dict_keys(['pos', 'cell', 'cell2', 'y', 'z', 'u', 'x', 'edge_index', 'edge_attr', 'edge_index_rr', 'edge_attr_rr', 'edge_index_rv', 'edge_attr_rv', 'cell_offsets', 'n_atoms'])

In [ ]:
r = 5.0
n_neighbors = 50
cell = sample.cell
pos = sample.pos


In [ ]:
loader = DataLoader([sample], batch_size=1, shuffle=False)


In [ ]:
batch = next(iter(loader))


Comparing the ASE primitive_neighbor_list routine with OCP's optimized torch implementation


In [ ]:
from matdeeplearn.preprocessor.helpers import *


In [ ]:
(
    edge_index_ase,
    cell_offsets_ase,
    edge_weights_ase,
    edge_vec_ase,
) = calculate_edges_all_neighbors(True, r, n_neighbors, "", cell, pos)

first_idex (8089,)


In [ ]:
sample.z.shape

torch.Size([257])

In [ ]:
sample.z

tensor([ 30,  30,  30,  30,   8,   8,   8,   8,   8,   8,   8,   8,   8,   8,
          8,   8,   8,   6,   6,   6,   6,   6,   6,   6,   6,   6,   6,   6,
          6,   6,   6,   6,   6,   6,   6,   6,   6,   6,   6,   6,   6, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100,
        100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 100, 1

In [ ]:
sample.edge_index_rv[0]

tensor(1)

In [ ]:
edge_index = torch.cat([sample.edge_index_rv, sample.edge_index_rr], dim=1)
edge_weight = torch.randn(edge_index.shape[1])

src_edges = edge_index[0]
atom_indices = sample.z.reshape(-1, 1).expand(-1, len(src_edges))
src_index = src_edges.reshape(1, -1).expand(len(atom_indices), -1)

# encode outgoing edges for each atom (neighbors)
res = torch.argwhere(src_edges == atom_indices).transpose(0, 1)

# unique, idx, counts = torch.unique(
#     res[0], dim=0, sorted=True, return_inverse=True, return_counts=True
# )
# _, ind_sorted = torch.sort(idx, stable=True)
# cum_sum = counts.cumsum(0)
# cum_sum = torch.cat((torch.tensor([0]), cum_sum[:-1]))

# # divide neighboring indices by atom
# first_indices = ind_sorted[cum_sum]
# neighbors_list = torch.tensor_split(res[1], first_indices[1:])

In [ ]:
edge_index = torch.cat([sample.edge_index_rv, sample.edge_index_rr], dim=1)
edge_weight = torch.abs(torch.randn(edge_index.shape[1]) + 1)

In [ ]:
from torch_geometric.utils import remove_self_loops

In [ ]:
src_edges = edge_index[0]
atom_indices = sample.z.reshape(-1, 1).expand(-1, len(src_edges))
src_index = src_edges.reshape(1, -1).expand(len(atom_indices), -1)

res = src_edges == atom_indices
expanded_weights = edge_weight.expand(len(atom_indices), -1)

weights = res * expanded_weights
_, indices = torch.topk(weights, k=n_neighbors, largest=False, dim=1)

# convert indices into edge index pairs
sources = torch.arange(len(atom_indices)).reshape(-1, 1).expand(-1, n_neighbors)
neighbor_edges = torch.stack([sources, indices], dim=2).reshape(-1, 2)

# remove duplicate entries
# mask = weights.flatten()[neighbor_edges[1]] != 0
# neighbor_edges[0, mask] = neighbor_edges[1, mask]
# neighbor_edges, _ = remove_self_loops(neighbor_edges)

In [ ]:
weights.flatten()

tensor([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 

In [ ]:
neighbor_edges.shape

torch.Size([12850, 2])

In [ ]:
torch.unique(neighbor_edges, dim=0).shape

torch.Size([12850, 2])

In [ ]:
edge_mask

tensor([False, False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False,  True,  True,  True,  True,
         True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
         True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
        False, False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False,  True,  True,  True,  True,
         True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
         True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
        False, False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False,  True,  True, 

In [ ]:
neighbor_edges.shape

torch.Size([2, 12850])

In [ ]:
indices.shape

torch.Size([257, 50])

In [ ]:
edge_weight.shape

torch.Size([1545])

In [ ]:
edge_weight[res].shape

torch.Size([2, 1526])

In [ ]:
print(src_edges.shape, atom_indices.shape)


torch.Size([257, 1545]) torch.Size([257, 1545])


In [ ]:
first_indices


tensor([   0,   36,   72,  108,  144,  182,  220,  258,  296,  334,  372,  410,
         448,  486,  524,  562,  600,  638,  675,  712,  749,  786,  823,  860,
         897,  934,  971, 1008, 1045, 1082, 1119, 1156, 1193, 1230, 1267, 1304,
        1341, 1378, 1415, 1452, 1489])

In [ ]:
neighbors_list


(tensor([ 661,  662,  663,  664,  665,  666,  667,  668,  669,  670,  671,  672,
         673,  674,  675,  676,  677,  678,  679,  680,  681,  682,  683,  684,
         685,  686,  687, 1449, 1450, 1451, 1452, 1453, 1454, 1455, 1456, 1457]), tensor([ 661,  662,  663,  664,  665,  666,  667,  668,  669,  670,  671,  672,
         673,  674,  675,  676,  677,  678,  679,  680,  681,  682,  683,  684,
         685,  686,  687, 1449, 1450, 1451, 1452, 1453, 1454, 1455, 1456, 1457]), tensor([ 661,  662,  663,  664,  665,  666,  667,  668,  669,  670,  671,  672,
         673,  674,  675,  676,  677,  678,  679,  680,  681,  682,  683,  684,
         685,  686,  687, 1449, 1450, 1451, 1452, 1453, 1454, 1455, 1456, 1457]), tensor([ 661,  662,  663,  664,  665,  666,  667,  668,  669,  670,  671,  672,
         673,  674,  675,  676,  677,  678,  679,  680,  681,  682,  683,  684,
         685,  686,  687, 1449, 1450, 1451, 1452, 1453, 1454, 1455, 1456, 1457]), tensor([ 172,  173,  174,  175,

In [ ]:
edge_index_ocp, cell_ocp, neighbor_image_ocp = radius_graph_pbc(
    r, n_neighbors, pos, cell.view(1, 3, 3), sample.n_atoms
)


In [ ]:
cd_matrix, offsets, _ = get_cutoff_distance_matrix(pos, cell, r, n_neighbors, "cpu")
edge_index_or, edge_weight_or = dense_to_sparse(cd_matrix)

torch.Size([257, 206])


In [ ]:
edge_index_ase, _ = edge_index_ase.sort(dim=1)
edge_index_ocp, _ = edge_index_ocp.sort(dim=1)
edge_index_or, _ = edge_index_or.sort(dim=1)


In [ ]:
edge_index_or.shape

torch.Size([2, 7831])

In [ ]:
edge_index_ase.shape

torch.Size([2, 7832])

In [ ]:
edge_index_or == edge_index_ocp

tensor([[ True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  